In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import preprocessing
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.preprocessing.image import load_img
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Conv2D, Dropout, Flatten, MaxPooling2D,BatchNormalization
import os
import pandas as pd
import numpy as np
# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/mood-detection/Dataset/labels.txt
/kaggle/input/mood-detection/Dataset/test/surprise/265708769.png
/kaggle/input/mood-detection/Dataset/test/surprise/853493510.png
/kaggle/input/mood-detection/Dataset/test/surprise/180748518.png
/kaggle/input/mood-detection/Dataset/test/surprise/121055828.png
/kaggle/input/mood-detection/Dataset/test/surprise/722443276.png
/kaggle/input/mood-detection/Dataset/test/surprise/726536869.png
/kaggle/input/mood-detection/Dataset/test/surprise/257586962.png
/kaggle/input/mood-detection/Dataset/test/surprise/928373399.png
/kaggle/input/mood-detection/Dataset/test/surprise/611883075.png
/kaggle/input/mood-detection/Dataset/test/surprise/829658531.png
/kaggle/input/mood-detection/Dataset/test/surprise/231572859.png
/kaggle/input/mood-detection/Dataset/test/surprise/857463060.png
/kaggle/input/mood-detection/Dataset/test/surprise/677491196.png
/kaggle/input/mood-detection/Dataset/test/surprise/898997797.png
/kaggle/input/mood-detection/Dataset/test/

In [ ]:

TRAIN_DIR = '/kaggle/input/mood-detection/Dataset/train'

TEST_DIR = '/kaggle/input/mood-detection/Dataset/test'

def createdataframe(dir):
    image_paths = []
    labels = []
    for label in os.listdir(dir):
        for imagename in os.listdir(os.path.join(dir, label)):
            image_paths.append(os.path.join(dir, label, imagename))
            labels.append(label)
        print(label, "completed")
    return image_paths, labels
train = pd.DataFrame()
train['image'], train['label'] = createdataframe(TRAIN_DIR)
print(train)
test = pd.DataFrame()
test['image'], test['label'] = createdataframe(TEST_DIR)
print(test)
from tqdm.notebook import tqdm


In [ ]:
from keras.preprocessing.image import save_img
from keras.preprocessing.image import img_to_array

def extract_features(images):
    features = []
    for image in tqdm(images):
         
        img = load_img(image, color_mode='grayscale')
        
        img = np.array(img)
        features.append(img)
    features = np.array(features)
    features = features.reshape(len(features), 48, 48, 1)
    return features

In [ ]:
train_features = extract_features(train['image'])
test_features = extract_features(test['image'])

In [ ]:
x_train = train_features / 255.0
x_test = test_features / 255.0

In [ ]:
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
le.fit(train['label'])
y_train = le.transform(train['label'])
y_test = le.transform(test['label'])
y_train = to_categorical(y_train, num_classes=7)
y_test = to_categorical(y_test, num_classes=7)


In [ ]:

model = Sequential()

model.add(Conv2D(32, (5, 5), strides = (1, 1), name = 'conv0', input_shape = (32, 32, 1)))

model.add(BatchNormalization(axis = 3, name = 'bn0'))
model.add(Activation('relu'))

model.add(MaxPooling2D((2, 2), name='max_pool'))
model.add(Conv2D(64, (3, 3), strides = (1,1), name="conv1"))
model.add(Activation('relu'))
model.add(AveragePooling2D((3, 3), name='avg_pool'))

model.add(GlobalAveragePooling2D())
model.add(Dense(300, activation="relu", name='rl'))
model.add(Dropout(0.5))
model.add(Dense(1,activation='sigmoid', name='sm'))

In [ ]:
conv_model = convolutional_model((48, 48, 1))
conv_model.compile(optimizer='adam',
                  loss='categorical_crossentropy',
                  metrics=['accuracy'])
conv_model.summary()
train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train)).batch(48)
test_dataset = tf.data.Dataset.from_tensor_slices((x_test, y_test)).batch(48)
history = conv_model.fit(train_dataset, epochs=100, validation_data=test_dataset)    


In [ ]:
model_json = model.to_json()
with open("mooddetector.json", 'w') as json_file:
    json_file.write(model_json)
model.save("mooddetector.h5")

In [ ]:
label = ['anger', 'disgust', 'fear', 'happiness', 'neutral', 'sadness', 'surprise']
def ef(image):
    img = load_img(image, color_mode='grayscale')
    feature = np.array(img)
    feature = feature.reshape(1, 48, 48, 1)
    return feature / 255.0

In [ ]:
image = '/kaggle/input/mood-detection/Dataset/train/anger/44151112.png'
print("original image is of anger")
img = ef(image)
pred = model.predict(img)
pred_label = label[pred.argmax()]
print("model prediction is ", pred_label)